In [2]:
import tensorflow as tf
from tensorflow.keras.models import load_model
import librosa
import IPython
import numpy as np
from numpy.lib.stride_tricks import sliding_window_view
import pandas as pd

from utils import extract_mfcc

In [22]:
# model = load_model('models/v4.hdf5')
# model = load_model('models/v7 (with_self_collected_data_undersampled).hdf5')
model = load_model('models/v8 (all).hdf5')

In [23]:
sr=16000

In [24]:
IPython.display.Audio('test_audios/test2.mp3', rate=sr)

In [31]:
y, sr = librosa.load('test audios/test2.mp3', sr=sr)

C:\Users\nurha\.conda\envs\audio_env\lib\site-packages\librosa\core\audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")


In [32]:
def unfold(array, size, step):
    """
    params:
       array: 1d array 
       size : size of each chunk
       step : windowing size
    """
    assert array.ndim == 1, f"Not implemented yet, expecting 1d array but got {array.ndim}d"
    return sliding_window_view(array, window_shape=size)[::step]

In [33]:
splitted_audios = unfold(y, 3*sr, 3*sr)

In [34]:
df = pd.DataFrame()

In [35]:
for audio in splitted_audios:
    mfcc = librosa.feature.mfcc(audio, sr, n_mfcc=13)
    probability = model.predict(np.expand_dims(mfcc, axis=0))
    label = 1 if probability > 0.42 else 0
    df = df.append({
        'audio': audio,
        'mfcc': mfcc,
        'probability': probability,
        'label': label
    }, ignore_index=True)

In [36]:
df

audio  label  \
0   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...    0.0   
1   [-0.002885679, 0.00039088549, 0.0007556422, 0....    1.0   
2   [0.0040602963, 0.0017522754, -0.0034530866, -0...    1.0   
3   [-0.00027004414, -0.0001732661, -0.00038776564...    1.0   
4   [2.5852745e-05, 3.040674e-05, 7.2158455e-06, 1...    1.0   
5   [-0.0028397117, -0.004544267, -0.0054703685, -...    0.0   
6   [0.0037885685, 0.001870697, 0.00049403927, 0.0...    0.0   
7   [0.002555634, 0.0029904724, 0.0037979116, 0.00...    0.0   
8   [0.002482839, 0.0019740406, 0.0019426991, 0.00...    1.0   
9   [1.2920149e-05, 2.3758856e-05, 1.5798341e-06, ...    0.0   
10  [0.0025702768, -0.0012613214, -0.0015485769, -...    0.0   
11  [0.0001297863, -0.0055003096, -0.010657773, -0...    1.0   
12  [-0.001581279, -0.0016735859, -0.0028775746, -...    0.0   
13  [0.0008080094, 0.00038522424, 0.00013529528, -...    0.0   
14  [0.000110072484, 0.00014466947, 0.0002515603, ...    0.0   
15  [0.0062395, -0.0012426244, -0.0076504983, -0.0...    0.0   
16  [2.8194747e-05, 6.183609e-06, -1.5322315e-05, ...    0.0   
17  [0.00078616804, 0.00096722593, 0.0011408747, 0...    0.0   
18  [-0.0017226447, -0.0015591691, -0.0015630949, ...    0.0   

                                                 mfcc      probability  
0   [[-798.76886, -738.0197, -680.4776, -679.1856,...  [[0.058065474]]  
1   [[-407.43134, -380.82016, -357.71524, -355.153...    [[0.9329426]]  
2   [[-448.1994, -406.09583, -401.44415, -407.3443...    [[0.5451344]]  
3   [[-427.68756, -426.83847, -456.32422, -466.194...   [[0.42433387]]  
4   [[-734.0655, -710.47656, -633.43774, -524.9939...     [[0.740322]]  
5   [[-397.21204, -446.7354, -578.618, -633.75494,...  [[0.017762184]]  
6   [[-408.1469, -408.7184, -354.85992, -281.81555...    [[0.3230719]]  
7   [[-476.3398, -477.1567, -484.55786, -483.4164,...   [[0.07892111]]  
8   [[-339.803, -343.93616, -348.8992, -360.10492,...    [[0.5909811]]  
9   [[-624.1176, -435.52322, -346.4079, -314.78778...  [[0.044017613]]  
10  [[-530.3982, -527.90454, -492.74457, -421.0634...  [[0.025378317]]  
11  [[-411.21167, -426.2419, -472.54904, -569.9856...    [[0.4519214]]  
12  [[-255.36891, -235.71999, -255.70645, -318.868...  [[0.063242674]]  
13  [[-410.85947, -333.6734, -283.54538, -272.5166...   [[0.26656228]]  
14  [[-696.8106, -661.34033, -627.3179, -627.7137,...   [[0.14964843]]  
15  [[-420.31097, -456.25357, -588.9265, -695.6585...   [[0.02588746]]  
16  [[-706.47974, -656.78, -638.16504, -661.45624,...   [[0.02945131]]  
17  [[-500.8826, -530.2626, -613.4645, -583.8497, ...   [[0.22591177]]  
18  [[-448.0921, -461.33365, -473.06165, -473.4678...   [[0.31675172]]

In [37]:
for i, audio in enumerate(df['audio']):
    print(df.iloc[i]['label'], df.iloc[i]['probability'])
    IPython.display.display(IPython.display.Audio(audio, rate=sr))

0.0 [[0.05806547]]


1.0 [[0.9329426]]


1.0 [[0.5451344]]


1.0 [[0.42433387]]


1.0 [[0.740322]]


...

0.0 [[0.14964843]]


0.0 [[0.02588746]]


0.0 [[0.02945131]]


0.0 [[0.22591177]]


0.0 [[0.31675172]]
